#Détection de la langue d'un texte avec un réseau convolutionnel

**Le but de ce projet est de programmer un classifieur permettant de détecter la langue d'un texte à partir de la fréquence des bigrammes de ce dernier.**

## Préparation des données

On récupère les corpus de d'apprentissage et de test

In [1]:
%%bash
rm train.tgz
wget http://pageperso.lif.univ-mrs.fr/~alexis.nasr/Ens/MASCO_Apprentissage_Automatique/train.tgz
tar xvfz train.tgz


train/
train/uk_iu-ud-train.txt
train/zh_gsd-ud-train.txt
train/la_ittb-ud-train.txt
train/af_afribooms-ud-train.txt
train/be_hse-ud-train.txt
train/cs_cac-ud-train.txt
train/fro_srcmf-ud-train.txt
train/hsb_ufal-ud-train.txt
train/mt_mudt-ud-train.txt
train/mr_ufal-ud-train.txt
train/en_lines-ud-train.txt
train/fr_sequoia-ud-train.txt
train/cu_proiel-ud-train.txt
train/fi_ftb-ud-train.txt
train/ro_rrt-ud-train.txt
train/sv_talbanken-ud-train.txt
train/hi_hdtb-ud-train.txt
train/en_esl-ud-train.txt
train/pl_sz-ud-train.txt
train/cs_pdt-ud-train.txt
train/bg_btb-ud-train.txt
train/el_gdt-ud-train.txt
train/fr_partut-ud-train.txt
train/sme_giella-ud-train.txt
train/da_ddt-ud-train.txt
train/qhe_hiencs-ud-train.txt
train/lv_lvtb-ud-train.txt
train/no_nynorsk-ud-train.txt
train/cs_fictree-ud-train.txt
train/en_ewt-ud-train.txt
train/ga_idt-ud-train.txt
train/fr_spoken-ud-train.txt
train/ca_ancora-ud-train.txt
train/sl_sst-ud-train.txt
train/ur_udtb-ud-train.txt
train/got_proiel-ud-train.tx

rm: cannot remove 'train.tgz': No such file or directory
--2019-04-12 15:26:58--  http://pageperso.lif.univ-mrs.fr/~alexis.nasr/Ens/MASCO_Apprentissage_Automatique/train.tgz
Resolving pageperso.lif.univ-mrs.fr (pageperso.lif.univ-mrs.fr)... 139.124.22.27
Connecting to pageperso.lif.univ-mrs.fr (pageperso.lif.univ-mrs.fr)|139.124.22.27|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 29281190 (28M) [application/x-gzip]
Saving to: ‘train.tgz’

     0K .......... .......... .......... .......... ..........  0%  157K 3m2s
    50K .......... .......... .......... .......... ..........  0%  329K 2m14s
   100K .......... .......... .......... .......... ..........  0%  129M 89s
   150K .......... .......... .......... .......... ..........  0%  176M 67s
   200K .......... .......... .......... .......... ..........  0%  334K 70s
   250K .......... .......... .......... .......... ..........  1%  126M 59s
   300K .......... .......... .......... .......... ..........  1

**On fait la liste des fichiers dont on veut se servir pour construire les données d'apprentissage.**
**A chaque corpus on associe un identificateur de la langue (en, fr, it ...)**

In [0]:
l_corpus_train=[
['en', './train/en_partut-ud-train.txt'],
['fr', './train/fr_sequoia-ud-train.txt'],
['it', './train/it_partut-ud-train.txt'],
['nl', './train/nl_lassysmall-ud-train.txt'],
['sl', './train/sl_sst-ud-train.txt'],
['es', './train/es_ancora-ud-train.txt'],
['pt', './train/pt_bosque-ud-train.txt'],
['de', './train/de_gsd-ud-train.txt'],
['ca', './train/ca_ancora-ud-train.txt']
]

**On construit un dictionnaire qui associe à chaque langue un identifiant numérique**

In [3]:
def calculeCodeLangues(l_corpus):
    nbLangues = 0
    codeLangue = { }

    for corpus in l_corpus:
        idLangue = corpus[0]
        fichierCorpus = corpus[1]
        if not idLangue in codeLangue :
          print('langue :', idLangue, 'code = ', nbLangues)
          codeLangue[idLangue] = nbLangues
          nbLangues += 1
    return codeLangue
  
codeLangues = calculeCodeLangues(l_corpus_train)
  

langue : en code =  0
langue : fr code =  1
langue : it code =  2
langue : nl code =  3
langue : sl code =  4
langue : es code =  5
langue : pt code =  6
langue : de code =  7
langue : ca code =  8


In [4]:
import random
import sys

        

def extract_seq(corpus, longueurSeq, nbSeq):
    try:
        fic = open(corpus, 'r')
    except IOError:
        print("le fichier", corpus, "n'existe pas")
        return None

    corpus_str = fic.read()
    corpus_str = corpus_str.replace("\n", " ")
    longueur_corpus = len(corpus_str)
#    print("longueur corpus = ", longueur_corpus)
    fic.close()
    
    lSeq = []
    for numSeq in range(nbSeq):
        position = random.randint(0,longueur_corpus - longueurSeq)
        lSeq.append(corpus_str[position:position+longueurSeq])
    return lSeq

def process_corpus(l_corpus, longueurSeq, nbSeq, fichierXSortie, fichierYSortie) :
    try:
        ficXOut = open(fichierXSortie, 'w')
    except IOError:
        print("le fichier", fichierXSortie, "n'existe pas")
        exit
    try:
        ficYOut = open(fichierYSortie, 'w')
    except IOError:
        print("le fichier", fichierYSortie, "n'existe pas")
        exit

    for corpus in l_corpus:
        idLangue = corpus[0]
        fichierCorpus = corpus[1]
        print('traite corpus', fichierCorpus)
        lSeq = extract_seq(fichierCorpus, longueurSeq, nbSeq)
        for seq in lSeq:
            print(idLangue, file = ficYOut)
            print(seq, file = ficXOut)
            #print(idLangue, ' ', seq)
    ficXOut.close
    ficYOut.close
    
longueurSeq = 100
nbSeq = 1000
process_corpus(l_corpus_train, longueurSeq, nbSeq, 'trainX.dat', 'trainY.dat')

traite corpus ./train/en_partut-ud-train.txt
traite corpus ./train/fr_sequoia-ud-train.txt
traite corpus ./train/it_partut-ud-train.txt
traite corpus ./train/nl_lassysmall-ud-train.txt
traite corpus ./train/sl_sst-ud-train.txt
traite corpus ./train/es_ancora-ud-train.txt
traite corpus ./train/pt_bosque-ud-train.txt
traite corpus ./train/de_gsd-ud-train.txt
traite corpus ./train/ca_ancora-ud-train.txt


**On met en forme les données de manière à pouvoir les fournir au réseau de neurones pour l'apprentissage**

In [0]:
import numpy as np
import sys

def char_code(c):
    if 'a' <= c and c <= 'z':
        return ord(c) - ord('a')
    elif c == ' ':
        return 26
    else :
        return 27
    
def lectureDonneesX(nomFichier):
    try:
        fic = open(nomFichier, 'r')
    except IOError:
        print("le fichier", nomFichier, "n'existe pas")
        return None

    lx = []
    for ligne in fic:
        ligne = ligne.strip('\n\r')
        #print("ligne =", ligne)
        resultat = [char_code(c) for c in ligne]
        lx.append(resultat)
    fic.close()
    x_train = np.array(lx, dtype="int")
    print(len(x_train), "exemples lus")
    #print(x_train)
    return(x_train)

def lectureDonneesY(nomFichier, codeLangue):
    try:
        fic = open(nomFichier, 'r')
    except IOError:
        print("le fichier", nomFichier, "n'existe pas")
        return None

    nbLangues = len(codeLangue.keys()) 
    ly = []
    for ligne in fic:
        ligne = ligne.strip('\n\r')
        v = [0] * nbLangues
        v[codeLangue[ligne]] = 1
        #print("langue = ", ligne, "vecteur = ", v)  
        ly.append(v)
    fic.close()

    
    y_train = np.array(ly, dtype="int")
    print(len(y_train), "exemples lus")
    #print(y_train)
    return (y_train)





**On construit la structure du réseau et on fait l'apprentissage**

In [0]:
from keras.models import Sequential
from keras.layers import Dense, Activation, Dropout, Conv1D, MaxPooling1D, Reshape, Flatten

nombre_de_filtres = 512
taille_du_noyau = 5
x_train = lectureDonneesX('trainX.dat')
y_train = lectureDonneesY('trainY.dat', codeLangues)

t = np.arange(len(x_train))
np.random.shuffle(t)
x_train = x_train[t]
y_train = y_train[t]

nbLangues = len(codeLangues.keys()) 
print('nbLangues =', nbLangues)
print('longueur des séquences = ', longueurSeq)
print('taille du noyau = ', taille_du_noyau)
print('nombre de filtres = ', nombre_de_filtres)


model = Sequential()
model.add(Conv1D(kernel_size=taille_du_noyau, filters=nombre_de_filtres, activation='relu', input_shape=(longueurSeq,1), padding='same'))
model.add(MaxPooling1D(pool_size=longueurSeq))
model.add(Flatten())
model.add(Dense(units=nbLangues, activation='softmax'))
model.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])
print(model.summary())
# x_train and y_train are Numpy arrays 
x_train = np.reshape(x_train, x_train.shape + (1,))
#print("x train shape = ", x_train.shape)

#print(x_train)
#print(x_train)
#y_train = np.expand_dims(y_train, axis=2)
model.fit(x_train, y_train, epochs=30, batch_size=20, validation_split=0.2,)



Using TensorFlow backend.


9000 exemples lus
9000 exemples lus
nbLangues = 9
longueur des séquences =  100
taille du noyau =  5
nombre de filtres =  512
Instructions for updating:
Colocations handled automatically by placer.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv1d_1 (Conv1D)            (None, 100, 512)          3072      
_________________________________________________________________
max_pooling1d_1 (MaxPooling1 (None, 1, 512)            0         
_________________________________________________________________
flatten_1 (Flatten)          (None, 512)               0         
_________________________________________________________________
dense_1 (Dense)              (None, 9)                 4617      
Total params: 7,689
Trainable params: 7,689
Non-trainable params: 0
_________________________________________________________________
None
Instructions for updating:
Use tf.cast instead.
Train on 7200 samples

** On charge les données de test**

In [0]:
%%bash
rm test.tgz
wget http://pageperso.lif.univ-mrs.fr/~alexis.nasr/Ens/MASCO_Apprentissage_Automatique/test.tgz
tar xvfz test.tgz


In [0]:
l_corpus_test=[
['en', './test/en_partut-ud-test.txt'],
['fr', './test/fr_sequoia-ud-test.txt'],
['it', './test/it_partut-ud-test.txt'],
['nl', './test/nl_lassysmall-ud-test.txt'],
['sl', './test/sl_sst-ud-test.txt'],
['es', './test/es_ancora-ud-test.txt'],
['pt', './test/pt_bosque-ud-test.txt'],
['de', './test/de_gsd-ud-test.txt'],
['ca', './test/ca_ancora-ud-test.txt']
]

In [0]:
extract_bigrams(l_corpus_test, 'random', 500, 10, 'test.dat')
(x_test, y_test) = lectureDonnees('test.dat', codeLangues)

**On évalue le modèle sur les données de test**

In [0]:
l_id = [''] * len(codeLangues)
for (key, val) in (codeLangues.items()):
  #print("key =", key , 'val =', val)
  l_id[int(val)] = key

In [0]:

def argmax(l):
  i = 1
  max = l[0] 
  arg = 0
  while i < len(l) :
    if l[i] > max :
      max = l[i]
      arg = i
    i = i + 1
  return arg

score = model.evaluate(x_test, y_test)
print('test.dat score = ', score)
l_pred = model.predict(x_test, batch_size=None, verbose=1, steps=None)
i = 0
while i < len(l_pred) :
  #print(l_pred[i])
  predicted = l_id[argmax(l_pred[i])]
  gold = l_id[argmax(y_test[i])]
  print('pred =', predicted, 'gold =', gold)
  i = i + 1
